In [304]:
import os
import sklearn
import pandas as pd
import csv

In [305]:
n_gram_value = 5

In [306]:
def get_ngrams(input_list, n):    
    return zip(*[input_list[i:] for i in range(n)])


In [307]:
def getAllPossibleWords(file_path): 
    possible_words=[]
    with open(file_path) as f:
        for line in f:
            for word in line.split():
                possible_words.append(word)     
   # possible_words = map(lambda x : unidecode.unidecode(x),possible_words)
    for c in ['`',"[","]","(",")","\"",".","''",","]:
        possible_words = map(lambda x: x.replace(c,""),possible_words)
        
    possible_words = map(lambda x: x.replace('&','And'),possible_words)
    #possible_words = map(lambda x: x.replace('of','Of'),possible_words)
    possible_words=filter(lambda x:len(x)>0,possible_words)    
    
    return possible_words

In [308]:
def getListFromFiles(filename):
    file_path = os.path.join(os.getcwd(),filename)
    info_list = []
    with open(file_path) as f:
        for line in f:
            for word in line.split():
                info_list.append(word)
    return info_list

In [309]:
def writeToCsv(processed_list):
    with open("output-sreejita.csv",'wb') as resultFile:
        wr = csv.writer(resultFile, dialect='excel')
        for row in processed_list:
            print row
            wr.writerows(row)

In [310]:
def preprocessing(possible_words,doc_id):    
    suffix_list = getListFromFiles("company-suffixes.txt")
    prefix_list = getListFromFiles("company-prefixes.txt")    
    common_words = getListFromFiles("common-words.txt")
    preprocessed_list =[]    
    marked_list=[]
    word_number=len(possible_words)
    for i in range(5,0,-1):
        word_count=0
        ngram_list = get_ngrams(possible_words,i)
        for ngram in ngram_list:            
            #print ngram   
            
            #if markup is both at the beginning or at the end of the word group accept and label as 1
            if(len(ngram)>1 and '<markup>' in ngram[0] and '</markup>' in ngram[len(ngram)-1] and
              all((word[0].isupper() or "markup" in word) for word in ngram) and 
              ["<markup>" in word for word in ngram].count(True)==1):
                preprocessed_list.append([' '.join(ngram),doc_id,word_count,word_count+i-1,1])
            
            #get all instances of format <markup>Microsoft</markup>
            if(len(ngram)==1 and '</markup>' in ngram[0] and '<markup>' in ngram[0]):
                preprocessed_list.append([' '.join(ngram),doc_id,word_count,word_count+i-1,1])            
                    
            else:
                #prune away all n grams with non uppercase first character
                if(all(word[0].isupper() and "markup" not in word for word in ngram)):       
                    
                    # prune common words
                    if(any(word not in common_words for word in ngram)):                        
                        preprocessed_list.append([' '.join(ngram),doc_id,word_count,word_count+i-1,0])

                    #prune unigrams 
                    elif(i==1 and word_number> word_count+1):                        
                        
                        #add the unigram to the list if the next word begins with lower case
                        if(possible_words[word_count+1][0].islower()):
                            preprocessed_list.append([' '.join(ngram),doc_id,word_count,word_count+i-1,0])  
            word_count = word_count+1
    return preprocessed_list    

In [311]:
base_directory = os.path.dirname(os.getcwd())
data_directory = os.path.join(base_directory,"Dataset","Sreejita")
file_list = os.listdir(data_directory)
possible_words=[]
processed_list=[]
count=0
#doc_id = 101
for file in file_list:
    doc_id = file[0:3]
    #print(doc_id)
    #if(int(doc_id)!=95):
    #    continue    
    possible_words = getAllPossibleWords(os.path.join(data_directory,file))     
    
    #start from here .. processessed list has the structure[[word,doc_id,word_count_start,word_count_end,label]]
    processed_list.append(preprocessing(possible_words,doc_id))
    writeToCsv(processed_list)   
  

[['Chief Executive Officer Robert Gannicott', '201', 109, 113, 0], ['Executive Officer Robert Gannicott Gannicott', '201', 110, 114, 0], ['Chief Executive Officer Robert', '201', 109, 112, 0], ['Executive Officer Robert Gannicott', '201', 110, 113, 0], ['Officer Robert Gannicott Gannicott', '201', 111, 114, 0], ['<markup>Aber Diamond Corp</markup>', '201', 0, 2, 1], ['Toronto Stock Exchange', '201', 18, 20, 0], ['<markup>Rio Tinto Plc</markup>', '201', 95, 97, 1], ['Chief Executive Officer', '201', 109, 111, 0], ['Executive Officer Robert', '201', 110, 112, 0], ['Officer Robert Gannicott', '201', 111, 113, 0], ['Robert Gannicott Gannicott', '201', 112, 114, 0], ['Harry Winston', '201', 7, 8, 0], ['Toronto Stock', '201', 18, 19, 0], ['Stock Exchange', '201', 19, 20, 0], ['Northwest Territories', '201', 82, 83, 0], ['Canadian Press', '201', 104, 105, 0], ['Chief Executive', '201', 109, 110, 0], ['Executive Officer', '201', 110, 111, 0], ['Officer Robert', '201', 111, 112, 0], ['Robert Ga

[['Chief Executive Officer Robert Gannicott', '201', 109, 113, 0], ['Executive Officer Robert Gannicott Gannicott', '201', 110, 114, 0], ['Chief Executive Officer Robert', '201', 109, 112, 0], ['Executive Officer Robert Gannicott', '201', 110, 113, 0], ['Officer Robert Gannicott Gannicott', '201', 111, 114, 0], ['<markup>Aber Diamond Corp</markup>', '201', 0, 2, 1], ['Toronto Stock Exchange', '201', 18, 20, 0], ['<markup>Rio Tinto Plc</markup>', '201', 95, 97, 1], ['Chief Executive Officer', '201', 109, 111, 0], ['Executive Officer Robert', '201', 110, 112, 0], ['Officer Robert Gannicott', '201', 111, 113, 0], ['Robert Gannicott Gannicott', '201', 112, 114, 0], ['Harry Winston', '201', 7, 8, 0], ['Toronto Stock', '201', 18, 19, 0], ['Stock Exchange', '201', 19, 20, 0], ['Northwest Territories', '201', 82, 83, 0], ['Canadian Press', '201', 104, 105, 0], ['Chief Executive', '201', 109, 110, 0], ['Executive Officer', '201', 110, 111, 0], ['Officer Robert', '201', 111, 112, 0], ['Robert Ga

[['The Markit CDX North America', '226', 31, 35, 0], ['Markit CDX North America Investment', '226', 32, 36, 0], ['CDX North America Investment Grade', '226', 33, 37, 0], ['North America Investment Grade Index', '226', 34, 38, 0], ['The Markit CDX North', '226', 31, 34, 0], ['Markit CDX North America', '226', 32, 35, 0], ['CDX North America Investment', '226', 33, 36, 0], ['North America Investment Grade', '226', 34, 37, 0], ['America Investment Grade Index', '226', 35, 38, 0], ['<markup>Goldman Sachs Group Inc</markup>', '226', 231, 234, 1], ['The Markit CDX', '226', 31, 33, 0], ['Markit CDX North', '226', 32, 34, 0], ['CDX North America', '226', 33, 35, 0], ['North America Investment', '226', 34, 36, 0], ['America Investment Grade', '226', 35, 37, 0], ['Investment Grade Index', '226', 36, 38, 0], ['<markup>Deutsche Bank AG</markup>', '226', 64, 66, 1], ['New York The', '226', 68, 70, 0], ['<markup>Standard And Poor</markup>', '226', 135, 137, 1], ['Markit LCDX Series', '226', 219, 221

[['Chief Executive Officer Bruce Williamson', '231', 202, 206, 0], ['<markup>Calyon Securities USA Inc</markup>', '231', 148, 151, 1], ['Chief Executive Officer Bruce', '231', 202, 205, 0], ['Executive Officer Bruce Williamson', '231', 203, 206, 0], ['<markup>RBC Capital Markets</markup>', '231', 58, 60, 1], ['New York Johong', '231', 62, 64, 0], ['Chief Executive Officer', '231', 202, 204, 0], ['Executive Officer Bruce', '231', 203, 205, 0], ['Officer Bruce Williamson', '231', 204, 206, 0], ['<markup>Dynegy Inc</markup>', '231', 0, 1, 1], ['Lasan Johong', '231', 53, 54, 0], ['New York', '231', 62, 63, 0], ['York Johong', '231', 63, 64, 0], ['Gordon Howald', '231', 143, 144, 0], ['Securities USA', '231', 149, 150, 0], ['New York', '231', 153, 154, 0], ['Chief Executive', '231', 202, 203, 0], ['Executive Officer', '231', 203, 204, 0], ['Officer Bruce', '231', 204, 205, 0], ['Bruce Williamson', '231', 205, 206, 0], ['David Byford', '231', 233, 234, 0], ['DYN', '231', 2, 2, 0], ['US', '23

[['Chief Executive Officer Montie Brewer', '203', 22, 26, 0], ['Chief Financial Officer Francois Laurin', '203', 149, 153, 0], ['Chief Executive Officer Montie', '203', 22, 25, 0], ['Executive Officer Montie Brewer', '203', 23, 26, 0], ['<markup>ACE Aviation Holdings Inc</markup>', '203', 61, 64, 1], ['Chief Financial Officer Francois', '203', 149, 152, 0], ['Financial Officer Francois Laurin', '203', 150, 153, 0], ['Chief Executive Officer', '203', 22, 24, 0], ['Executive Officer Montie', '203', 23, 25, 0], ['Officer Montie Brewer', '203', 24, 26, 0], ['Mont Tremblant Quebec', '203', 52, 54, 0], ['<markup>Transat AT Inc</markup>', '203', 130, 132, 1], ['Chief Financial Officer', '203', 149, 151, 0], ['Financial Officer Francois', '203', 150, 152, 0], ['Officer Francois Laurin', '203', 151, 153, 0], ['CEO Joseph Randell', '203', 213, 215, 0], ['<markup>Air Canada</markup>', '203', 0, 1, 1], ['Chief Executive', '203', 22, 23, 0], ['Executive Officer', '203', 23, 24, 0], ['Officer Montie

...

[['Chief Executive Officer Robert Gannicott', '201', 109, 113, 0], ['Executive Officer Robert Gannicott Gannicott', '201', 110, 114, 0], ['Chief Executive Officer Robert', '201', 109, 112, 0], ['Executive Officer Robert Gannicott', '201', 110, 113, 0], ['Officer Robert Gannicott Gannicott', '201', 111, 114, 0], ['<markup>Aber Diamond Corp</markup>', '201', 0, 2, 1], ['Toronto Stock Exchange', '201', 18, 20, 0], ['<markup>Rio Tinto Plc</markup>', '201', 95, 97, 1], ['Chief Executive Officer', '201', 109, 111, 0], ['Executive Officer Robert', '201', 110, 112, 0], ['Officer Robert Gannicott', '201', 111, 113, 0], ['Robert Gannicott Gannicott', '201', 112, 114, 0], ['Harry Winston', '201', 7, 8, 0], ['Toronto Stock', '201', 18, 19, 0], ['Stock Exchange', '201', 19, 20, 0], ['Northwest Territories', '201', 82, 83, 0], ['Canadian Press', '201', 104, 105, 0], ['Chief Executive', '201', 109, 110, 0], ['Executive Officer', '201', 110, 111, 0], ['Officer Robert', '201', 111, 112, 0], ['Robert Ga

[['Chief Executive Officer Robert Milton', '202', 75, 79, 0], ['<markup>Kohlberg Kravis Roberts And Co</markup>', '202', 110, 114, 1], ['<markup>ACE Aviation Holdings Inc</markup>', '202', 0, 3, 1], ['<markup>Jazz Air Income Fund</markup>', '202', 14, 17, 1], ['<markup>West Face Capital Inc</markup>', '202', 37, 40, 1], ['Chief Executive Officer Robert', '202', 75, 78, 0], ['Executive Officer Robert Milton', '202', 76, 79, 0], ['<markup>Sunrise Partners LP</markup>', '202', 42, 44, 1], ['Chief Executive Officer', '202', 75, 77, 0], ['Executive Officer Robert', '202', 76, 78, 0], ['Officer Robert Milton', '202', 77, 79, 0], ['Kravis Roberts And', '202', 111, 113, 0], ['<markup>Aeroplan Income Fund</markup>', '202', 129, 131, 1], ['Toronto Stock Exchange', '202', 152, 154, 0], ['Aviation Holdings', '202', 1, 2, 0], ['Air Income', '202', 15, 16, 0], ['<markup>Jazz Air</markup>', '202', 22, 23, 1], ['Face Capital', '202', 38, 39, 0], ['<markup>ACE Aviation</markup>', '202', 54, 55, 1], ['<

[['<markup>St Jude Medical Inc</markup>', '214', 26, 29, 1], ['<markup>Cambridge Heart Inc</markup>', '214', 0, 2, 1], ['Robert P Khederian', '214', 149, 151, 0], ['Jude Medical', '214', 27, 28, 0], ['<markup>Cambridge Heart</markup>', '214', 37, 38, 1], ['<markup>The Bedford</markup>', '214', 81, 82, 1], ['<markup>Cambridge Heart</markup>', '214', 108, 109, 1], ['<markup>St Jude</markup>', '214', 114, 115, 1], ['March It', '214', 120, 121, 0], ['Robert P', '214', 149, 150, 0], ['P Khederian', '214', 150, 151, 0], ['<markup>Cambridge Heart</markup>', '214', 156, 157, 1], ['Heart', '214', 1, 1, 0], ['CAMH', '214', 3, 3, 0], ['Jude', '214', 27, 27, 0], ['Medical', '214', 28, 28, 0], ['STJ', '214', 30, 30, 0], ['Bloomberg', '214', 63, 63, 0], ['Massachusetts', '214', 83, 83, 0], ['T-wave', '214', 89, 89, 0], ['March', '214', 120, 120, 0], ['It', '214', 121, 121, 0], ['Robert', '214', 149, 149, 0], ['P', '214', 150, 150, 0], ['Khederian', '214', 151, 151, 0]]
[['<markup>Baltic Beverages Ho

[['Chief Executive Officer Robert Gannicott', '201', 109, 113, 0], ['Executive Officer Robert Gannicott Gannicott', '201', 110, 114, 0], ['Chief Executive Officer Robert', '201', 109, 112, 0], ['Executive Officer Robert Gannicott', '201', 110, 113, 0], ['Officer Robert Gannicott Gannicott', '201', 111, 114, 0], ['<markup>Aber Diamond Corp</markup>', '201', 0, 2, 1], ['Toronto Stock Exchange', '201', 18, 20, 0], ['<markup>Rio Tinto Plc</markup>', '201', 95, 97, 1], ['Chief Executive Officer', '201', 109, 111, 0], ['Executive Officer Robert', '201', 110, 112, 0], ['Officer Robert Gannicott', '201', 111, 113, 0], ['Robert Gannicott Gannicott', '201', 112, 114, 0], ['Harry Winston', '201', 7, 8, 0], ['Toronto Stock', '201', 18, 19, 0], ['Stock Exchange', '201', 19, 20, 0], ['Northwest Territories', '201', 82, 83, 0], ['Canadian Press', '201', 104, 105, 0], ['Chief Executive', '201', 109, 110, 0], ['Executive Officer', '201', 110, 111, 0], ['Officer Robert', '201', 111, 112, 0], ['Robert Ga

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [312]:
ngram = ('<markup>Gazprom', 'Lukoil</markup>')
if(len(ngram)>1 and '<markup>' in ngram[0] and '</markup>' in ngram[len(ngram)-1] and
              all((word[0].isupper() or "markup" in word) for word in ngram) and 
              ["<markup>" in word for word in ngram].count(True)==1):
    print "hallo"


hallo


In [313]:
["markup" in word for word in ngram].count(True)==2

True

In [298]:
import pycountry
country_names = []
for country in pycountry.countries:
    country_names.append(country.name)
    if hasattr(country,'common_name'):
        country_names.append(country.common_name)
    if hasattr(country, 'official_name'):
        country_names.append(country.official_name)

country_names.append("America")
country_names.append("Korea")
country_names.append("South Korea")
country_names.append("North Korea")
country_names.append("U.S.")
country_names.append("Russia")

if "Russia" in country_names:
    print "YES"
    
continent_list = ['Asia', 'Africa', 'South America', 'North America', 'Antarctica', 'Europe', 'Australia']

YES


In [299]:
cities = []
with open('world-cities.csv', 'r') as inp:
        for row in csv.reader(inp):
            if(row and row[3] != "" and row[0]!="name"):
                cities.append(row[0])

cities.append('Bombay')
cities.append('New York')
if "New York City" in cities:
    print "YES"

YES


In [300]:
desig = open('designations.txt').read().split('\n')
desig_lower = [x.lower() for x in desig]
print desig_lower

['chief executive officer', 'chief financial officer', 'co-chief executive', 'chief investment officer', 'analyst', 'ceo', 'cio', 'cto', 'cfo', 'manager', 'director', 'president', 'vice-president', 'vice president', 'chief', 'executive', 'officer', 'officers', 'analysts', 'managers', 'directors', 'co-chief', 'co chief']


In [301]:
stock_x = open('stock-exchange-list.txt').read().split('\n')
unigram_prune = open('unigram-prune-neg.txt').read().split('\n')
special_char = [';', ',', ':', '?']
prune = open('pruning-neg.txt').read().split('\n') 
prune_lower = [x.lower() for x in prune]
suffixes = open('company-suffixes.txt').read().split('\n')
prefixes = open('company-prefixes.txt').read().split('\n')
print suffixes
rows = 0
len(processed_list)
for doc in processed_list:
    rows += len(doc)
    
print rows
print unigram_prune

['Inc', 'Inc.', 'Plc', 'Plc.', 'AG', 'A/S', 'NV', 'AB', 'Co', 'Co.', 'Group', 'Ltd', 'Ltd.', 'Fund', 'LP', 'Corp.', 'Corp', 'SA', 'LLC', 'LLC.', 'Financial', 'Capital', 'Stockbrokers', 'LLP', 'LLP.', 'Enterprise', 'Securities', 'Pte', 'Pte.', 'Bhd', 'Bhd.', 'NL', 'Partners', 'Holdings', 'Markets', 'GmbH', 'Trust', 'Bros', 'NV', 'SpA', 'Equities', 'Cos', 'Cos.', 'AFK', 'Associates', 'LP', 'LP.', 'Bank', 'HF', 'ASA', 'SAB', 'Groupe', 'Resources', 'GOK', 'SAA', 'Investments', 'AS', 'International', 'Industries', 'Management', 'BV']
5223
['The', 'These', 'There', 'They', 'It', 'When', 'A', 'An', 'Under', 'Over', 'Between', 'On', 'In', 'Out', 'Why', 'Where', 'How', 'What', 'We', 'His', 'Her', 'Him', 'Their', 'Our', 'He', 'She', 'I', 'At', 'November', 'December', 'October', 'September', 'March', 'April', 'May', 'June', 'July', 'August', 'January', 'February', 'Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec', 'Finance', 'Financial', 'And']


In [302]:
new_proc_list = []
pruned_list = []
for doc in processed_list:
    for inst in doc:
        if inst[4] == 0:
            if inst[0] in country_names or inst[0] in continent_list or inst[0] in cities or inst[0] in stock_x:
                pruned_list.append(inst)
            elif inst[0].endswith('n') and inst[0][:-1] in country_names or str in continent_list:
                pruned_list.append(inst)
            elif "based" in inst[0]:
                pruned_list.append(inst)
            elif any(d in inst[0].lower().split() for d in desig_lower):
                pruned_list.append(inst)
            elif any(p in inst[0].lower().split() for p in prune_lower):
                pruned_list.append(inst)
            elif '(' in inst[0] or ')' in inst[0]:
                pruned_list.append(inst)
            elif any(c in inst[0] for c in special_char):
                pruned_list.append(inst)
            elif len(inst[0].split()) == 1:
                if len(inst[0]) == 1:
                    pruned_list.append(inst)
                elif inst[0] in unigram_prune:
                    pruned_list.append(inst)
                elif inst[0] == inst[0].upper():
                    pruned_list.append(inst)
                elif inst[0] in suffixes or inst[0] in prefixes:
                    pruned_list.append(inst)
                else:
                    new_proc_list.append(inst)
            else:
                new_proc_list.append(inst)
        else:
            new_proc_list.append(inst)
            
                
print len(pruned_list)
#writeToCsv(processed_list)
print len(new_proc_list)
print len(pruned_list) + len(new_proc_list)

2142
3081
5223


In [303]:
with open("output_sreejita_pruned.csv", "w") as output:
    writer = csv.writer(output, lineterminator='\n')
    for val in new_proc_list:
        writer.writerow(val)

[['<markup>Aber Diamond Corp</markup>', '201', 0, 2, 1], ['<markup>Rio Tinto Plc</markup>', '201', 94, 96, 1], ['Robert Gannicott Gannicott', '201', 111, 113, 0], ['Toronto Stock', '201', 18, 19, 0], ['Northwest Territories', '201', 81, 82, 0], ['Canadian Press', '201', 103, 104, 0], ['Robert Gannicott', '201', 111, 112, 0], ['Gannicott Gannicott', '201', 112, 113, 0], ['<markup>Alcan Inc</markup>', '201', 154, 155, 1], ["<markup>Aber</markup>'s", '201', 60, 60, 1], ['<markup>Aber</markup>', '201', 70, 70, 1], ['<markup>Aber</markup>', '201', 107, 107, 1], ['<markup>Aber</markup>', '201', 116, 116, 1], ["<markup>Rio</markup>'s", '201', 124, 124, 1], ['<markup>Rio</markup>', '201', 139, 139, 1]]
[['<markup>Aber Diamond Corp</markup>', '201', 0, 2, 1], ['<markup>Rio Tinto Plc</markup>', '201', 94, 96, 1], ['Robert Gannicott Gannicott', '201', 111, 113, 0], ['Toronto Stock', '201', 18, 19, 0], ['Northwest Territories', '201', 81, 82, 0], ['Canadian Press', '201', 103, 104, 0], ['Robert Ga

[['<markup>China Banking Regulatory Commission</markup>', '223', 51, 54, 1], ['<markup>China Construction Bank Corp</markup>', '223', 140, 143, 1], ['And Commercial Bank', '223', 18, 20, 0], ['And Commercial', '223', 18, 19, 0], ['Commercial Bank', '223', 19, 20, 0], ['Liu Mingkang', '223', 46, 47, 0], ['Banking Regulatory', '223', 52, 53, 0], ['A July', '223', 93, 94, 0], ['Construction Bank', '223', 141, 142, 0], ['<markup>ICBC</markup>', '223', 128, 128, 1]]
[['<markup>China Banking Regulatory Commission</markup>', '223', 51, 54, 1], ['<markup>China Construction Bank Corp</markup>', '223', 140, 143, 1], ['And Commercial Bank', '223', 18, 20, 0], ['And Commercial', '223', 18, 19, 0], ['Commercial Bank', '223', 19, 20, 0], ['Liu Mingkang', '223', 46, 47, 0], ['Banking Regulatory', '223', 52, 53, 0], ['A July', '223', 93, 94, 0], ['Construction Bank', '223', 141, 142, 0], ['<markup>ICBC</markup>', '223', 128, 128, 1]]
[['<markup>China Banking Regulatory Commission</markup>', '223', 51,

[['US Canada Europe', '237', 79, 81, 0], ['<markup><markup>Ormat Industries Ltd</markup>', '237', 165, 167, 1], ['<markup>Gazit-Globe Ltd</markup>', '237', 0, 1, 1], ['US Canada', '237', 79, 80, 0], ['Canada Europe', '237', 80, 81, 0], ['Israel The', '237', 83, 84, 0], ['Europe We', '237', 112, 113, 0], ['Chairman Chaim', '237', 129, 130, 0], ['US The', '237', 180, 181, 0], ['<markup>Gazit-Globe</markup>', '237', 72, 72, 1], ['<markup>Gazit-Globe</markup>', '237', 154, 154, 1], ['<markup>Gazit-Globe</markup>', '237', 226, 226, 1]]
[['US Canada Europe', '237', 79, 81, 0], ['<markup><markup>Ormat Industries Ltd</markup>', '237', 165, 167, 1], ['<markup>Gazit-Globe Ltd</markup>', '237', 0, 1, 1], ['US Canada', '237', 79, 80, 0], ['Canada Europe', '237', 80, 81, 0], ['Israel The', '237', 83, 84, 0], ['Europe We', '237', 112, 113, 0], ['Chairman Chaim', '237', 129, 130, 0], ['US The', '237', 180, 181, 0], ['<markup>Gazit-Globe</markup>', '237', 72, 72, 1], ['<markup>Gazit-Globe</markup>', '

[['<markup>Investment Property Databank Ltd</markup>', '252', 117, 120, 1], ['<markup>Liberty International Plc</markup>', '252', 0, 2, 1], ['Property Databank', '252', 118, 119, 0], ['David Fischel', '252', 163, 164, 0], ['London The', '252', 180, 181, 0], ['The FTSE', '252', 200, 201, 0], ['Real Estate', '252', 203, 204, 0], ['<markup>Liberty</markup>', '252', 78, 78, 1], ["<markup>Liberty</markup>'s", '252', 94, 94, 1], ['<markup>Liberty</markup>', '252', 171, 171, 1]]
[['<markup>Investment Property Databank Ltd</markup>', '252', 117, 120, 1], ['<markup>Liberty International Plc</markup>', '252', 0, 2, 1], ['Property Databank', '252', 118, 119, 0], ['David Fischel', '252', 163, 164, 0], ['London The', '252', 180, 181, 0], ['The FTSE', '252', 200, 201, 0], ['Real Estate', '252', 203, 204, 0], ['<markup>Liberty</markup>', '252', 78, 78, 1], ["<markup>Liberty</markup>'s", '252', 94, 94, 1], ['<markup>Liberty</markup>', '252', 171, 171, 1]]
[['<markup>Investment Property Databank Ltd</m

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

